In [1]:
from shapely.geometry import Point, Polygon, MultiPolygon
from unidecode import unidecode
from plotly import graph_objects as go
import pandas as pd
import geopandas as gpd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import dotenv
import warnings
import os

In [2]:
sns.set_style("darkgrid")
warnings.filterwarnings("ignore")

dotenv.load_dotenv()

True

In [22]:
parques = gpd.read_file('../data/external/parques_bogota/parques_bogota.geojson')

In [4]:
apartamentos = pd.read_csv('../data/interim/metrocuadrado/venta_apartamentos_bogota.csv')
localidades = gpd.read_file('../data/external/localidades_bogota/loca.shp')
barrios = gpd.read_file('../data/external/barrios_bogota/barrios.geojson')

apartamentos.shape, localidades.shape, barrios.shape

((11836, 44), (20, 7), (3871, 11))

In [4]:
estaciones_tm = pd.read_csv('../data/external/estaciones_troncales_transmilenio/estaciones_troncales_transmilenio.csv')
paraderos_sitp = pd.read_csv('../data/external/paraderos_zonales_SITP/Paraderos_Zonales_del_SITP.csv')

estaciones_tm.shape, paraderos_sitp.shape

((149, 26), (7618, 18))

In [5]:
def normalize(text):
    try:
        return unidecode(text).upper()
    except:
        return text

## Agregando información exacta de la ubicación de los apartamentos

- Localidad
- Barrio

In [8]:
# asignar localidad a cada apartamento si las coordenadas(latitud, longitud) del apartamento estan dentro de los limites de la localidad
def get_localidad(row):
    try:
        point = Point(row['longitud'], row['latitud'])
        for i, localidad in localidades.iterrows():
            if point.within(localidad['geometry']):
                return unidecode(localidad['LocNombre']).upper()
        return np.nan
    except:
        return np.nan
    
apartamentos['localidad'] = apartamentos.apply(get_localidad, axis=1)

In [9]:
apartamentos['localidad'].unique()

array(['USAQUEN', 'TEUSAQUILLO', nan, 'KENNEDY', 'CHAPINERO',
       'BARRIOS UNIDOS', 'SUBA', 'PUENTE ARANDA', 'SANTA FE',
       'SAN CRISTOBAL', 'ENGATIVA', 'FONTIBON', 'LOS MARTIRES',
       'CIUDAD BOLIVAR', 'CANDELARIA', 'BOSA', 'RAFAEL URIBE URIBE',
       'USME', 'ANTONIO NARINO', 'TUNJUELITO'], dtype=object)

In [10]:
barrios['localidad'] = barrios['localidad'].apply(lambda x: normalize(x))
barrios['barriocomu'] = barrios['barriocomu'].apply(lambda x: normalize(x))

barrios.loc[barrios['localidad'] == 'RAFAEL URIBE', 'localidad'] = 'RAFAEL URIBE URIBE'

barrios['localidad'].unique()

array(['FONTIBON', 'ENGATIVA', 'USAQUEN', 'RAFAEL URIBE URIBE',
       'TEUSAQUILLO', 'TUNJUELITO', 'USME', 'SAN CRISTOBAL', 'SANTA FE',
       nan, 'BARRIOS UNIDOS', 'PUENTE ARANDA', 'CANDELARIA', 'KENNEDY',
       'BOSA', 'CIUDAD BOLIVAR', 'LOS MARTIRES', 'CHAPINERO',
       'ANTONIO NARINO'], dtype=object)

In [11]:
fig = px.scatter_mapbox(
    apartamentos.loc[(apartamentos['localidad'] == 'CHAPINERO') & (apartamentos['precio'] < 8e9)],
    lat='latitud', 
    lon='longitud', 
    color='precio', 
    zoom=10, 
    height=500,
    hover_name='localidad',
    hover_data=['area_m2', 'habitaciones', 'baños', 'estrato'],
    color_continuous_scale=px.colors.sequential.Viridis,
)

fig.update_layout(
    mapbox=dict(
        accesstoken=os.getenv('MAPBOX_TOKEN'),
        style='dark',
        center=dict(
            lat=4.60971,
            lon=-74.08175
        )
    )
)

fig.update_layout(margin={'r': 0, 't': 0, 'l': 0, 'b': 0})
fig.show()

In [12]:
barrios.head(3)

objectid  cod_loc localidad         estado              barriocomu   
0       624        9  FONTIBON  SIN LEGALIZAR  URB. MONTEVIDEO MZ 13B  \
1       626       10  ENGATIVA     LEGALIZADO                SAN JUAN   
2       648        1   USAQUEN  SIN LEGALIZAR      TORRES DEL COUNTRY   

   cod_polbar    shape_area  shape_len  geo_shape   
0       90163  2.670969e-06   0.006991        NaN  \
1      100190  5.450524e-07   0.003002        NaN   
2       10243  4.217785e-07   0.002818        NaN   

                                        geo_point_2d   
0  {'lon': -74.1232389247289, 'lat': 4.6429720912...  \
1  {'lon': -74.11704770473668, 'lat': 4.680566490...   
2  {'lon': -74.0470897158071, 'lat': 4.7141192371...   

                                            geometry  
0  POLYGON ((-74.12214 4.64306, -74.12345 4.64148...  
1  POLYGON ((-74.11653 4.68041, -74.11668 4.68031...  
2  POLYGON ((-74.04760 4.71400, -74.04754 4.71443...

In [13]:
barrios[barrios['localidad'].isna()].plot(figsize=(3, 5))

<Axes: >

In [14]:
barrios.loc[barrios['localidad'].isna(), 'localidad'] = 'SUBA'

In [15]:
def get_barrio(row):
    try:
        point = Point(row['longitud'], row['latitud'])
        loca = row['localidad']
        barrios_localidad = barrios.loc[barrios['localidad'] == loca]
        for i, barrio in barrios_localidad.iterrows():
            if point.within(barrio['geometry']):
                return barrio['barriocomu']
            
        return np.nan
    except:
        return np.nan
    
apartamentos['barrio'] = apartamentos.apply(get_barrio, axis=1)

In [16]:
fig = px.scatter_mapbox(
    apartamentos,
    lat='latitud', 
    lon='longitud', 
    color='precio', 
    zoom=10, 
    height=500,
    hover_name='barrio',
    hover_data=['area_m2', 'habitaciones', 'baños', 'estrato', 'localidad'],
    color_continuous_scale=px.colors.sequential.Viridis,
)

fig.update_layout(
    mapbox=dict(
        accesstoken=os.getenv('MAPBOX_TOKEN'),
        style='dark',
        center=dict(
            lat=4.60971,
            lon=-74.08175
        )
    )
)

fig.update_layout(margin={'r': 0, 't': 0, 'l': 0, 'b': 0})
fig.show()

In [17]:
fig = px.scatter_mapbox(
    apartamentos.loc[(apartamentos['barrio'] == 'S.C. ANTIGUO COUNTRY') & (apartamentos['precio'] < 7e9)],
    lat='latitud', 
    lon='longitud', 
    color='precio', 
    zoom=10, 
    height=500,
    hover_name='barrio',
    hover_data=['area_m2', 'habitaciones', 'baños', 'estrato', 'localidad'],
    color_continuous_scale=px.colors.sequential.Viridis,
)

fig.update_layout(
    mapbox=dict(
        accesstoken=os.getenv('MAPBOX_TOKEN'),
        style='dark',
        center=dict(
            lat=4.60971,
            lon=-74.08175
        )
    )
)

fig.update_layout(margin={'r': 0, 't': 0, 'l': 0, 'b': 0})
fig.show()

## Agregar informacion sobre el transporte publico

In [18]:
estaciones_tm.head(3)

X         Y  objectid  numero_estacion nombre_estacion   
0 -74.074562  4.666341         1             7103       AV. Chile  \
1 -74.099048  4.646881         2             6103             CAN   
2 -74.078699  4.645396         3             7106          Campín   

   coordenada_x_estacion  coordenada_y_estacion ubicacion_estacion   
0           1.000327e+06           1.007756e+06        Kr 30 Cl 72  \
1           9.976100e+05           1.005604e+06         Carrera 60   
2           9.998678e+05           1.005440e+06        Kr 30 Cl 53   

  troncal_estacion  numero_vagones_estacion  ...  longitud_estacion   
0              NQS                        6  ...         -74.074562  \
1         Calle 26                        4  ...         -74.099048   
2              NQS                        2  ...         -74.078699   

                                 globalid  created_user  created_date   
0  {F055422B-BD16-4DCE-BEEF-2AD5D8D0D555}           NaN           NaN  \
1  {AD7C6926-90EC-428C-A4D8-46FBB826A717}           NaN           NaN   
2  {FE684396-CDD5-44E5-A998-85528256441F}           NaN           NaN   

   last_edited_user  last_edited_date  codigo_nodo_estacion componente_wifi   
0               NaN               NaN                  7103             NaN  \
1               NaN               NaN                  6103             NaN   
2               NaN               NaN                  7106             NaN   

   componente_aplificacion  log_replica  
0                      NaN          NaN  
1                      NaN          NaN  
2                      NaN          NaN  

[3 rows x 26 columns]

In [19]:
# distancia a la estacion de transmilenio mas cercana en metros
def get_distancia_estacion(row):
    try:
        point = Point(row['longitud'], row['latitud'])
        distancias = []
        for i, estacion in estaciones_tm.iterrows():
            distancias.append(point.distance(Point(estacion['X'], estacion['Y'])))
        return round(min(distancias), 2)
    except:
        return np.nan
    
apartamentos['distancia_estacion_tm_m'] = apartamentos.apply(get_distancia_estacion, axis=1)

In [20]:
import math

def haversine_m(lat1, lon1, lat2, lon2):
    r = 6371000 # radio de la tierra en metros

    lat1_rad = math.radians(lat1)
    lon1_rad = math.radians(lon1)
    lat2_rad = math.radians(lat2)
    lon2_rad = math.radians(lon2)

    delta_lat = lat2_rad - lat1_rad
    delta_lon = lon2_rad - lon1_rad

    # Fórmula del haversine
    a = math.sin(delta_lat/2) ** 2 + math.cos(lat1_rad) * math.cos(lat2_rad) * math.sin(delta_lon/2) ** 2
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1-a))
    distancia = r * c
    
    return distancia

In [21]:
def estacion_tm_cercana(row):
    try:
        point = Point(row['longitud'], row['latitud'])
        distancias = []
        for i, estacion in estaciones_tm.iterrows():
            distancias.append(haversine_m(row['latitud'], row['longitud'], estacion['Y'], estacion['X']))
        return estaciones_tm.loc[np.argmin(distancias), 'nombre_estacion']
    except:
        return np.nan
    
def get_distancia_estacion_m(row):
    try:
        point = Point(row['longitud'], row['latitud'])
        distancias = []
        for i, estacion in estaciones_tm.iterrows():
            distancias.append(haversine_m(row['latitud'], row['longitud'], estacion['Y'], estacion['X']))
        return min(distancias)
    except:
        return np.nan
    
apartamentos['estacion_tm_cercana'] = apartamentos.apply(estacion_tm_cercana, axis=1)
apartamentos['distancia_estacion_tm_m'] = apartamentos.apply(get_distancia_estacion_m, axis=1)

In [22]:
apartamentos['distancia_estacion_tm_m'] = apartamentos['distancia_estacion_tm_m'].apply(lambda x: round(x, 2))

In [23]:
apartamentos['distancia_estacion_tm_m'].describe()

count    1.183000e+04
mean     1.602507e+05
std      1.133484e+06
min      1.530000e+00
25%      5.542075e+02
50%      1.176910e+03
75%      1.760975e+03
max      1.244730e+07
Name: distancia_estacion_tm_m, dtype: float64

In [24]:
fig = px.scatter_mapbox(
    apartamentos.loc[apartamentos['distancia_estacion_tm_m'] <= 500],
    lat='latitud', 
    lon='longitud', 
    color='precio', 
    zoom=10, 
    height=500,
    hover_name='barrio',
    hover_data=['area_m2', 'habitaciones', 'baños', 'estrato', 'localidad', 'distancia_estacion_tm_m', 'estacion_tm_cercana'],
    color_continuous_scale=px.colors.sequential.Viridis,
)

fig.add_trace(
    go.Scattermapbox(
        lat=estaciones_tm['Y'],
        lon=estaciones_tm['X'],
        mode='markers',
        marker=go.scattermapbox.Marker(
            size=10,
            color='red',
            opacity=0.7
        ),
        hoverinfo='text',
        text=estaciones_tm['nombre_estacion'],
        showlegend=False
    )
)

fig.update_layout(
    mapbox=dict(
        accesstoken=os.getenv('MAPBOX_TOKEN'),
        style='dark',
        center=dict(
            lat=4.60971,
            lon=-74.08175
        )
    )
)

fig.update_layout(margin={'r': 0, 't': 0, 'l': 0, 'b': 0})

fig.show()

In [25]:
def is_cerca_estacion(row):
    if row['distancia_estacion_tm_m'] <= 500:
        return 1
    else:
        return 0
    
apartamentos['cerca_estacion_tm'] = apartamentos.apply(is_cerca_estacion, axis=1)

In [26]:
paraderos_sitp.head(3)

X         Y  objectid  cenefa zona_sitp                nombre   
0 -74.063971  4.688481         1  001A00        00       C.C. Iserra 100  \
1 -74.045914  4.684091         2  001A01        01  Br. Rincón del Chicó   
2 -74.066350  4.759867         3  001A02        02       Gimnasio Iragua   

          via    direccion_bandera       localidad   longitud   latitud   
0      AC 100       AC 100 - KR 54  Barrios Unidos -74.063971  4.688481  \
1      AC 100       AC 100 - KR 13         Usaquén -74.045914  4.684091   
2  AV. Boyacá  AV. Boyacá - AC 170            Suba -74.066350  4.759867   

  consecutivo_zona tipo_m_s                       consola   
0              001        M       AC 100 - KR 54 (001A00)  \
1              001        M       AC 100 - KR 13 (001A01)   
2              001        S  AV. Boyacá - AC 170 (001A02)   

                 panel                             audio zonas_nuevas   
0       AC 100 - KR 54      Avenida Calle 100 Carrera 54            C  \
1       AC 100 - KR 13      Avenida Calle 100 Carrera 13            B   
2  AV. Boyacá - AC 170  Avenida Boyacá Avenida Calle 170            C   

                                 globalid  
0  {1C1EDC47-96EB-4853-9189-97B765A8AF81}  
1  {F086C285-653E-452F-947B-792103055740}  
2  {9A771489-8D3B-41CD-9042-2E2250DCE844}

In [27]:
paraderos_sitp['nombre'] = paraderos_sitp['nombre'].apply(lambda x: normalize(x))
paraderos_sitp['consola'] = paraderos_sitp['consola'].apply(lambda x: normalize(x))
paraderos_sitp['localidad'] = paraderos_sitp['localidad'].apply(lambda x: normalize(x))

In [28]:
paraderos_sitp.localidad.unique()

array(['BARRIOS UNIDOS', 'USAQUEN', 'SUBA', 'TEUSAQUILLO', 'FONTIBON',
       'PUENTE ARANDA', 'KENNEDY', 'TUNJUELITO', 'RAFAEL URIBE',
       'SAN CRISTOBAL', 'ENGATIVA', 'CIUDAD BOLIVAR', 'SANTA FE',
       'LOS MARTIRES', 'USME', 'BOSA', 'ANTONIO NARINO', 'CHAPINERO',
       'CANDELARIA'], dtype=object)

In [29]:
paraderos_sitp.loc[paraderos_sitp['localidad'] == 'RAFAEL URIBE', 'localidad'] = 'RAFAEL URIBE URIBE'

In [30]:
def get_distancia_paradero_sitp_m(row):
    try:
        distancias = []
        for i, paradero in paraderos_sitp.iterrows():
            distancias.append(haversine_m(row['latitud'], row['longitud'], paradero['latitud'], paradero['longitud']))
        return min(distancias)
    except:
        return np.nan
    
def paradero_sitp_cercano(row):
    try:
        distancias = []
        for i, paradero in paraderos_sitp.iterrows():
            distancias.append(haversine_m(row['latitud'], row['longitud'], paradero['latitud'], paradero['longitud']))
        return paraderos_sitp.loc[np.argmin(distancias), 'nombre']
    except:
        return np.nan

In [31]:
apartamentos['distancia_paradero_sitp_m'] = apartamentos.apply(get_distancia_paradero_sitp_m, axis=1)
apartamentos['paradero_sitp_cercano'] = apartamentos.apply(paradero_sitp_cercano, axis=1)

In [32]:
apartamentos['distancia_paradero_sitp_m'] = apartamentos['distancia_paradero_sitp_m'].apply(lambda x: round(x, 2))

In [33]:
apartamentos.distancia_paradero_sitp_m.describe()

count    1.183000e+04
mean     1.591086e+05
std      1.133183e+06
min      1.250000e+00
25%      7.973500e+01
50%      1.292600e+02
75%      2.044075e+02
max      1.244434e+07
Name: distancia_paradero_sitp_m, dtype: float64

In [37]:
fig = px.scatter_mapbox(
    apartamentos.loc[apartamentos['distancia_paradero_sitp_m'] <= 250],
    lat='latitud',
    lon='longitud',
    color='precio',
    zoom=10,
    height=500,
    hover_name='barrio',
    hover_data=['area_m2', 'habitaciones', 'baños', 'estrato', 'localidad', 'distancia_paradero_sitp_m', 'paradero_sitp_cercano'],
    color_continuous_scale=px.colors.sequential.Viridis,
)

fig.add_trace(
    go.Scattermapbox(
        lat=paraderos_sitp['latitud'],
        lon=paraderos_sitp['longitud'],
        mode='markers',
        marker=go.scattermapbox.Marker(
            size=10,
            color='blue',
            opacity=0.7
        ),
        hoverinfo='text',
        text=paraderos_sitp['nombre'],
        showlegend=False
    )
)

fig.update_layout(
    mapbox=dict(
        accesstoken=os.getenv('MAPBOX_TOKEN'),
        style='dark',
        center=dict(
            lat=4.60971,
            lon=-74.08175
        )
    )
)

fig.update_layout(margin={'r': 0, 't': 0, 'l': 0, 'b': 0})

In [38]:
def is_cerca_paradero_sitp(row):
    if row['distancia_paradero_sitp_m'] <= 250:
        return 1
    else:
        return 0
    
apartamentos['cerca_paradero_sitp'] = apartamentos.apply(is_cerca_paradero_sitp, axis=1)

In [39]:
apartamentos.columns

Index(['precio', 'habitaciones', 'baños', 'estrato', 'codigo', 'antiguedad',
       'area_m2', 'administracion', 'parqueaderos', 'piso', 'amoblado',
       'sauna', 'jacuzzi', 'deposito', 'vista_exterior', 'closets',
       'calefaccion', 'estufa', 'vigilancia', 'numero_ascensores',
       'cerca_parque', 'cerca_transporte', 'cerca_centros_comerciales',
       'cerca_colegios_universidades', 'cerca_supermercados',
       'zona_residencial', 'sobre_via_secundaria', 'sobre_via_principal',
       'zc_zonas_verdes', 'zc_salon_comunal', 'zc_gimnasio', 'zc_zonas_bbq',
       'zc_zonas_infantiles', 'zc_cancha_squash', 'acceso_discapacitados',
       'vista_panoramica', 'terraza_balcon', 'area_terraza_balcon', 'terraza',
       'parqueadero_visitantes', 'latitud', 'longitud', 'descripcion',
       'localidad', 'barrio', 'distancia_estacion_tm_m', 'estacion_tm_cercana',
       'cerca_estacion_tm', 'distancia_paradero_sitp_m',
       'paradero_sitp_cercano', 'cerca_paradero_sitp'],
      dtype='

In [40]:
apartamentos.drop(columns=['cerca_transporte'], inplace=True)

In [41]:
apartamentos.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11836 entries, 0 to 11835
Data columns (total 50 columns):
 #   Column                        Non-Null Count  Dtype  
---  ------                        --------------  -----  
 0   precio                        11836 non-null  float64
 1   habitaciones                  11834 non-null  float64
 2   baños                         11820 non-null  float64
 3   estrato                       11806 non-null  float64
 4   codigo                        11836 non-null  object 
 5   antiguedad                    11829 non-null  object 
 6   area_m2                       11836 non-null  object 
 7   administracion                10623 non-null  float64
 8   parqueaderos                  10618 non-null  float64
 9   piso                          6464 non-null   float64
 10  amoblado                      11836 non-null  int64  
 11  sauna                         11836 non-null  int64  
 12  jacuzzi                       11836 non-null  int64  
 13  d

In [57]:
apartamentos.to_csv('../data/processed/metrocuadrado/venta_apartamentos_bogota.csv', index=False)